In [1]:
import numpy as np
from scipy import stats
from scipy import optimize
from scipy import special
from scipy.stats import qmc
import time
import plotly.graph_objects as go

In [7]:
a = 0.16222484
b = 0.09532564640
x_0 = 0.5
n = 100000

# Definindo a função f(x)
def f(x, a, b):
    return np.exp(-a*x) * np.cos(b*x)

#### Crude

In [3]:
def crude(f, a, b, n, tipo, seed):
    if tipo == "quase": # Gerador Quase-Aleatório
        sampler = qmc.Halton(d=1, scramble=True, seed=seed)
        lista_x = sampler.random(n)
    elif tipo == "pseudo":
        lista_x = np.random.uniform(low=0, high=1, size=n) # Gera uma amostra uniforme entre 0 e 1 com n elementos

    integral = np.mean(f(lista_x, a, b)) # Calcula a média dos valor de f(x)
    return integral

#### Hit-or-Miss

In [132]:
def hit_or_miss(f, a, b, n, tipo, seed):
    acerto = 0 # Mantém conta de quantos pontos estão dentro da área de f(x)

    if tipo == "quase": # Gerador Quase-Aleatório
        sampler = qmc.Halton(d=2, scramble=True, seed=seed)
        lista_pontos = sampler.random(n)

        for ponto in lista_pontos:
            if ponto[1]< f(ponto[0], a, b): # Verifica se está dentro
                acerto += 1

    elif tipo == "pseudo":
        lista_x = np.random.uniform(low=0, high=1, size=n) # Gera a coordenada do ponto x [0, 1]
        lista_y = np.random.uniform(low=0, high=1, size=n) # Gera a coordenada do ponto y [0, 1]

        for x, y in zip(lista_x, lista_y):
            if y < f(x, a, b): # Verifica se está dentro
                acerto += 1

    integral = acerto / n
    return integral

#### Importance Sampling

In [133]:
def beta(x, alpha, theta):
    return stats.beta.pdf(x, alpha, theta)/stats.beta.cdf(1, alpha, theta)

def gamma(x, shape, scale):
    return stats.gamma.pdf(x, a=shape, scale=scale)/stats.gamma.cdf(1, a=shape, scale=scale)

def weibull(x, shape, scale):
    return stats.weibull_min.pdf(x, c=shape, scale=scale)/stats.weibull_min.cdf(1, c=shape, scale=scale)

def importance_sample_simplificado(f, a, b, dist, n, tipo, seed):

    if dist == "beta":
        popt = [0.972, 1.016]
        if tipo == "quase": # Gerador Quase-Aleatório
            sampler_x = qmc.Halton(d=1, scramble=True, seed=seed)
            samples = sampler_x.random(n)

            for i in range(len(samples)):
                samples[i] = samples[i][0]

            samples = np.array(samples)
            lista_x = stats.beta.ppf(samples, popt[0], popt[1])

        elif tipo == "pseudo":
            samples = np.random.rand(n)

            escala = stats.beta.cdf(1, popt[0], popt[1]) # Serve para que os números gerados sejam no intervalo [0,1]
            samples = np.array(samples)
            lista_x = stats.beta.ppf(samples*escala, popt[0], popt[1])

        lista_x = np.array(lista_x)
        return np.mean(f(lista_x, a, b)/beta(lista_x, popt[0], popt[1]))
    
    elif dist == "gamma":
        popt = [1.000, 6.475]

        if tipo == "quase": # Gerador Quase-Aleatório
            sampler_x = qmc.Halton(d=1, scramble=True, seed=seed)
            samples = sampler_x.random(n)

            lista_x = []
            escala = stats.gamma.cdf(1, loc=0, a=popt[0], scale=popt[1]) # Serve para que os números gerados sejam no intervalo [0,1]

            for i in range(len(samples)):
                samples[i] = samples[i][0]

            samples = np.array(samples)
            lista_x = stats.gamma.ppf(samples*escala, loc=0, a=popt[0], scale=popt[1])

        elif tipo == "pseudo":
            samples = np.random.rand(n)

            escala = stats.gamma.cdf(1, loc=0, a=popt[0], scale=popt[1]) # Serve para que os números gerados sejam no intervalo [0,1]
            samples = np.array(samples)
            lista_x = stats.gamma.ppf(samples*escala, loc=0, a=popt[0], scale=popt[1])

        lista_x = np.array(lista_x)
        return np.mean(f(lista_x, a, b)/gamma(lista_x, shape=popt[0], scale=popt[1]))

    elif dist == "weibull":
        popt = [1.000, 6.488]

        if tipo == "quase": # Gerador Quase-Aleatório
            sampler_x = qmc.Halton(d=1, scramble=True, seed=seed)
            samples = sampler_x.random(n)

            escala = stats.weibull_min.cdf(1, loc=0, c=popt[0], scale=popt[1]) # Serve para que os números gerados sejam no intervalo [0,1]

            for i in range(len(samples)):
                samples[i] = samples[i][0]
            samples = np.array(samples)
            lista_x = stats.weibull_min.ppf(samples*escala, loc=0, c=popt[0], scale=popt[1])

        elif tipo == "pseudo":
            samples = np.random.rand(n)

            escala = stats.weibull_min.cdf(1, loc=0, c=popt[0], scale=popt[1]) # Serve para que os números gerados sejam no intervalo [0,1]
            samples = np.array(samples)
            lista_x = stats.weibull_min.ppf(samples*escala, loc=0, c=popt[0], scale=popt[1])

        lista_x = np.array(lista_x)
        return np.mean(f(lista_x, a, b)/weibull(lista_x, popt[0], popt[1]))

#### Control Variate

In [134]:
# Definindo o polinômio
def p(x, x_0, f, a, b):
    return f(x_0, a, b) - (a*np.exp(-a*x_0)*np.cos(b*x_0) + b*np.exp(-a*x_0)*np.sin(b*x_0))*(x - x_0)

# Definindo a integral de p(x)
def integral_p(x, x_0, f, a, b):
    return (f(x_0, a, b) + (a*np.exp(-a*x_0)*np.cos(b*x_0) + b*np.exp(-a*x_0)*np.sin(b*x_0))*x_0)*x - (a*np.exp(-a*x_0)*np.cos(b*x_0) + b*np.exp(-a*x_0)*np.sin(b*x_0))*(x**2)/2

def control_variate(f, a, b, p, x_0, n, tipo, seed):
    if tipo == "quase": # Gerador Quase-Aleatório
        sampler = qmc.Halton(d=1, scramble=True, seed=seed)
        lista_x = sampler.random(n)    
    elif tipo == "pseudo":
        lista_x = np.random.uniform(low=0, high=1, size=n) # Gera valores de x aleatórios

    lista_x = np.sort(lista_x)

    def funcao(f, a, b, p, x, x_0, integral_p): # Função que calcula f(x) - p(x) + integral(p(x) entre 0 e 1)
        parte_1 = f(x, a, b) - p(x, x_0, f, a, b)
        parte_2 = integral_p(1, x_0, f, a, b) - integral_p(0, x_0, f, a, b)
        return parte_1 + parte_2

    lista_resultados = funcao(f, a, b, p, lista_x, x_0, integral_p)

    return np.sum(lista_resultados)/n

### **Gráficos de Convergência**

In [136]:
armazenar_lista = []
armazenar_estimativas = []
cores = ['#000080', '#4682b4', '#add8e6']

fig = go.Figure()

for i in range(3):
    seed = int(time.time()) + i
    
    lista_quantidade_de_pontos = np.logspace(1, 6, num=25, dtype=int)
    armazenar_lista.append(lista_quantidade_de_pontos)

    estimativas = [abs((crude(f, a, b, n, 'quase', seed) - 0.9217620390808)/0.9217620390808) for n in lista_quantidade_de_pontos]
    armazenar_estimativas.append(estimativas)

    fig.add_trace(go.Scatter(x=lista_quantidade_de_pontos, y=estimativas, mode='lines+markers', name=f'Quase {i+1}', line=dict(color=cores[i])))

cores = ['#FF9999', '#FF6666', '#FF3333']
for i in range(3):
    seed = int(time.time()) + i
    
    lista_quantidade_de_pontos = np.logspace(1, 6, num=25, dtype=int)
    armazenar_lista.append(lista_quantidade_de_pontos)

    estimativas = [abs((crude(f, a, b, n, 'pseudo', seed) - 0.9217620390808)/0.9217620390808) for n in lista_quantidade_de_pontos]
    armazenar_estimativas.append(estimativas)

    fig.add_trace(go.Scatter(x=lista_quantidade_de_pontos, y=estimativas, mode='lines+markers', name=f'Pseudo {i+1}', line=dict(color=cores[i])))
    
fig.add_shape(
    type="line",
    x0=min(lista_quantidade_de_pontos),
    y0=0,
    x1=max(lista_quantidade_de_pontos),
    y1=0,
    line=dict(color="black", width=2, dash="dash"),
)

fig.update_xaxes(type="log")
fig.update_layout(
    title="Convergência do Crude Monte Carlo",
    xaxis_title="Número de Pontos",
    yaxis_title="Módulo do Erro Relativo",
    legend_title="Iteração",
)
fig.show()

In [137]:
armazenar_lista = []
armazenar_estimativas = []
cores = ['#000080', '#4682b4', '#add8e6']

fig = go.Figure()

for i in range(3):
    seed = int(time.time()) + i
    
    lista_quantidade_de_pontos = np.logspace(1, 6, num=25, dtype=int)
    armazenar_lista.append(lista_quantidade_de_pontos)

    estimativas = [abs((hit_or_miss(f, a, b, n, 'quase', seed) - 0.9217620390808)/0.9217620390808) for n in lista_quantidade_de_pontos]
    armazenar_estimativas.append(estimativas)

    fig.add_trace(go.Scatter(x=lista_quantidade_de_pontos, y=estimativas, mode='lines+markers', name=f'Quase {i+1}', line=dict(color=cores[i])))

cores = ['#FF9999', '#FF6666', '#FF3333']
for i in range(3):
    seed = int(time.time()) + i
    
    lista_quantidade_de_pontos = np.logspace(1, 6, num=25, dtype=int)
    armazenar_lista.append(lista_quantidade_de_pontos)

    estimativas = [abs((hit_or_miss(f, a, b, n, 'pseudo', seed) - 0.9217620390808)/0.9217620390808) for n in lista_quantidade_de_pontos]
    armazenar_estimativas.append(estimativas)

    fig.add_trace(go.Scatter(x=lista_quantidade_de_pontos, y=estimativas, mode='lines+markers', name=f'Pseudo {i+1}', line=dict(color=cores[i])))
    
fig.add_shape(
    type="line",
    x0=min(lista_quantidade_de_pontos),
    y0=0,
    x1=max(lista_quantidade_de_pontos),
    y1=0,
    line=dict(color="black", width=2, dash="dash"),
)

fig.update_xaxes(type="log")
fig.update_layout(
    title="Convergência do Hit-or-Miss Monte Carlo",
    xaxis_title="Número de Pontos",
    yaxis_title="Módulo do Erro Relativo",
    legend_title="Iteração",
)
fig.show()

In [138]:
armazenar_lista = []
armazenar_estimativas = []
cores = ['#000080', '#4682b4', '#add8e6']

fig = go.Figure()

for i in range(3):
    seed = int(time.time()) + i
    
    lista_quantidade_de_pontos = np.logspace(1, 6, num=25, dtype=int)
    armazenar_lista.append(lista_quantidade_de_pontos)

    estimativas = [abs((importance_sample_simplificado(f, a, b, 'gamma', n, 'quase', seed) - 0.9217620390808)/0.9217620390808) for n in lista_quantidade_de_pontos]
    armazenar_estimativas.append(estimativas)

    fig.add_trace(go.Scatter(x=lista_quantidade_de_pontos, y=estimativas, mode='lines+markers', name=f'Quase {i+1}', line=dict(color=cores[i])))

cores = ['#FF9999', '#FF6666', '#FF3333']
for i in range(3):
    seed = int(time.time()) + i
    
    lista_quantidade_de_pontos = np.logspace(1, 6, num=25, dtype=int)
    armazenar_lista.append(lista_quantidade_de_pontos)

    estimativas = [abs((importance_sample_simplificado(f, a, b, 'gamma', n, 'pseudo', seed) - 0.9217620390808)/0.9217620390808) for n in lista_quantidade_de_pontos]
    armazenar_estimativas.append(estimativas)

    fig.add_trace(go.Scatter(x=lista_quantidade_de_pontos, y=estimativas, mode='lines+markers', name=f'Pseudo {i+1}', line=dict(color=cores[i])))
    
fig.add_shape(
    type="line",
    x0=min(lista_quantidade_de_pontos),
    y0=0,
    x1=max(lista_quantidade_de_pontos),
    y1=0,
    line=dict(color="black", width=2, dash="dash"),
)

fig.update_xaxes(type="log")
fig.update_layout(
    title="Convergência do Importance Sampling (Gamma) Monte Carlo",
    xaxis_title="Número de Pontos",
    yaxis_title="Módulo do Erro Relativo",
    legend_title="Iteração",
)
fig.show()

In [139]:
armazenar_lista = []
armazenar_estimativas = []
cores = ['#000080', '#4682b4', '#add8e6']

fig = go.Figure()

for i in range(3):
    seed = int(time.time()) + i
    
    lista_quantidade_de_pontos = np.logspace(1, 6, num=25, dtype=int)
    armazenar_lista.append(lista_quantidade_de_pontos)

    estimativas = [abs((importance_sample_simplificado(f, a, b, 'beta', n, 'quase', seed) - 0.9217620390808)/0.9217620390808) for n in lista_quantidade_de_pontos]
    armazenar_estimativas.append(estimativas)

    fig.add_trace(go.Scatter(x=lista_quantidade_de_pontos, y=estimativas, mode='lines+markers', name=f'Quase {i+1}', line=dict(color=cores[i])))

cores = ['#FF9999', '#FF6666', '#FF3333']
for i in range(3):
    seed = int(time.time()) + i
    
    lista_quantidade_de_pontos = np.logspace(1, 6, num=25, dtype=int)
    armazenar_lista.append(lista_quantidade_de_pontos)

    estimativas = [abs((importance_sample_simplificado(f, a, b, 'beta', n, 'pseudo', seed) - 0.9217620390808)/0.9217620390808) for n in lista_quantidade_de_pontos]
    armazenar_estimativas.append(estimativas)

    fig.add_trace(go.Scatter(x=lista_quantidade_de_pontos, y=estimativas, mode='lines+markers', name=f'Pseudo {i+1}', line=dict(color=cores[i])))
    
fig.add_shape(
    type="line",
    x0=min(lista_quantidade_de_pontos),
    y0=0,
    x1=max(lista_quantidade_de_pontos),
    y1=0,
    line=dict(color="black", width=2, dash="dash"),
)

fig.update_xaxes(type="log")
fig.update_layout(
    title="Convergência do Importance Sampling (Beta) Monte Carlo",
    xaxis_title="Número de Pontos",
    yaxis_title="Módulo do Erro Relativo",
    legend_title="Iteração",
)
fig.show()

In [140]:
armazenar_lista = []
armazenar_estimativas = []
cores = ['#000080', '#4682b4', '#add8e6']

fig = go.Figure()

for i in range(3):
    seed = int(time.time()) + i
    
    lista_quantidade_de_pontos = np.logspace(1, 6, num=25, dtype=int)
    armazenar_lista.append(lista_quantidade_de_pontos)

    estimativas = [abs((importance_sample_simplificado(f, a, b, 'weibull', n, 'quase', seed) - 0.9217620390808)/0.9217620390808) for n in lista_quantidade_de_pontos]
    armazenar_estimativas.append(estimativas)

    fig.add_trace(go.Scatter(x=lista_quantidade_de_pontos, y=estimativas, mode='lines+markers', name=f'Quase {i+1}', line=dict(color=cores[i])))

cores = ['#FF9999', '#FF6666', '#FF3333']
for i in range(3):
    seed = int(time.time()) + i
    
    lista_quantidade_de_pontos = np.logspace(1, 6, num=25, dtype=int)
    armazenar_lista.append(lista_quantidade_de_pontos)

    estimativas = [abs((importance_sample_simplificado(f, a, b, 'weibull', n, 'pseudo', seed) - 0.9217620390808)/0.9217620390808) for n in lista_quantidade_de_pontos]
    armazenar_estimativas.append(estimativas)

    fig.add_trace(go.Scatter(x=lista_quantidade_de_pontos, y=estimativas, mode='lines+markers', name=f'Pseudo {i+1}', line=dict(color=cores[i])))
    
fig.add_shape(
    type="line",
    x0=min(lista_quantidade_de_pontos),
    y0=0,
    x1=max(lista_quantidade_de_pontos),
    y1=0,
    line=dict(color="black", width=2, dash="dash"),
)

fig.update_xaxes(type="log")
fig.update_layout(
    title="Convergência do Importance Sampling (Weibull) Monte Carlo",
    xaxis_title="Número de Pontos",
    yaxis_title="Módulo do Erro Relativo",
    legend_title="Iteração",
)
fig.show()

In [141]:
armazenar_lista = []
armazenar_estimativas = []
cores = ['#000080', '#4682b4', '#add8e6']

fig = go.Figure()

for i in range(3):
    seed = int(time.time()) + i
    
    lista_quantidade_de_pontos = np.logspace(1, 6, num=25, dtype=int)
    armazenar_lista.append(lista_quantidade_de_pontos)

    estimativas = [abs((control_variate(f, a, b, p, x_0, n, 'quase', seed) - 0.9217620390808)/0.9217620390808) for n in lista_quantidade_de_pontos]
    armazenar_estimativas.append(estimativas)

    fig.add_trace(go.Scatter(x=lista_quantidade_de_pontos, y=estimativas, mode='lines+markers', name=f'Quase {i+1}', line=dict(color=cores[i])))

cores = ['#FF9999', '#FF6666', '#FF3333']
for i in range(3):
    seed = int(time.time()) + i
    
    lista_quantidade_de_pontos = np.logspace(1, 6, num=25, dtype=int)
    armazenar_lista.append(lista_quantidade_de_pontos)

    estimativas = [abs((control_variate(f, a, b, p, x_0, n, 'pseudo', seed) - 0.9217620390808)/0.9217620390808) for n in lista_quantidade_de_pontos]
    armazenar_estimativas.append(estimativas)

    fig.add_trace(go.Scatter(x=lista_quantidade_de_pontos, y=estimativas, mode='lines+markers', name=f'Pseudo {i+1}', line=dict(color=cores[i])))
    
fig.add_shape(
    type="line",
    x0=min(lista_quantidade_de_pontos),
    y0=0,
    x1=max(lista_quantidade_de_pontos),
    y1=0,
    line=dict(color="black", width=2, dash="dash"),
)

fig.update_xaxes(type="log")
fig.update_layout(
    title="Convergência do Control Variate Monte Carlo",
    xaxis_title="Número de Pontos",
    yaxis_title="Módulo do Erro Relativo",
    legend_title="Iteração",
)
fig.show()

### **Distribuições e Histogramas**

In [142]:
lista = []
testes = 10**4
for m in range(testes):
    seed = int(time.time()) + m
    lista.append(crude(f, a, b, 1000, 'quase', seed))

media = np.mean(lista)
desvio_padrao = np.std(lista)

# Criando o histograma com Plotly
histograma = go.Histogram(
    x=lista,
    histnorm='probability',
    marker_color='darkblue',
    opacity=0.75,
    showlegend=False
)

layout = go.Layout(
    title='Distribuição das Estimativas da Integral por Crude Monte Carlo Quase-Aleatório',
    xaxis=dict(title='Valores Estimados'),
    yaxis=dict(title='Probabilidade'),
    bargap=0.1
)

# Adicionando uma linha para a média
linha_media = go.Scatter(
    x=[media, media],
    y=[0, 0.035],  # Ajuste conforme necessário
    mode='lines',
    line=dict(color='black', width=2, dash='dash'),
    name=f'Média: {media:.6f}'
)

# Adicionando linhas para o desvio padrão acima e abaixo da média
linha_desvio_superior = go.Scatter(
    x=[media + desvio_padrao, media + desvio_padrao],
    y=[0, 0.035],  # Ajuste conforme necessário
    mode='lines',
    line=dict(color='red', width=2, dash='dash'),  # Configuração da linha pontilhada
    name=f'Desvio Padrão: {desvio_padrao:.6f}'
)

linha_desvio_inferior = go.Scatter(
    x=[media - desvio_padrao, media - desvio_padrao],
    y=[0, 0.035],  # Ajuste conforme necessário
    mode='lines',
    line=dict(color='red', width=2, dash='dash'),  # Configuração da linha pontilhada
    showlegend=False
)

# Criando a figura
fig = go.Figure(data=[histograma, linha_media, linha_desvio_inferior, linha_desvio_superior], layout=layout)

# Mostrando o gráfico
fig.show()

In [143]:
lista = []
testes = 10**4
for m in range(testes):
    seed = int(time.time()) + m
    lista.append(crude(f, a, b, 1000, 'pseudo', seed))

media = np.mean(lista)
desvio_padrao = np.std(lista)

# Criando o histograma com Plotly
histograma = go.Histogram(
    x=lista,
    histnorm='probability',
    marker_color='darkblue',
    opacity=0.75,
    showlegend=False
)

layout = go.Layout(
    title='Distribuição das Estimativas da Integral por Crude Monte Carlo Pseudo-Aleatório',
    xaxis=dict(title='Valores Estimados'),
    yaxis=dict(title='Probabilidade'),
    bargap=0.1
)

# Adicionando uma linha para a média
linha_media = go.Scatter(
    x=[media, media],
    y=[0, 0.035],  # Ajuste conforme necessário
    mode='lines',
    line=dict(color='black', width=2, dash='dash'),
    name=f'Média: {media:.6f}'
)

# Adicionando linhas para o desvio padrão acima e abaixo da média
linha_desvio_superior = go.Scatter(
    x=[media + desvio_padrao, media + desvio_padrao],
    y=[0, 0.035],  # Ajuste conforme necessário
    mode='lines',
    line=dict(color='red', width=2, dash='dash'),  # Configuração da linha pontilhada
    name=f'Desvio Padrão: {desvio_padrao:.6f}'
)

linha_desvio_inferior = go.Scatter(
    x=[media - desvio_padrao, media - desvio_padrao],
    y=[0, 0.035],  # Ajuste conforme necessário
    mode='lines',
    line=dict(color='red', width=2, dash='dash'),  # Configuração da linha pontilhada
    showlegend=False
)

# Criando a figura
fig = go.Figure(data=[histograma, linha_media, linha_desvio_inferior, linha_desvio_superior], layout=layout)

# Mostrando o gráfico
fig.show()

In [144]:
lista = []
testes = 10**4
for m in range(testes):
    seed = int(time.time()) + m
    lista.append(hit_or_miss(f, a, b, 1000, 'quase', seed))

media = np.mean(lista)
desvio_padrao = np.std(lista)

# Criando o histograma com Plotly
histograma = go.Histogram(
    x=lista,
    histnorm='probability',
    marker_color='darkblue',
    opacity=0.75,
    showlegend=False
)

layout = go.Layout(
    title='Distribuição das Estimativas da Integral por Hit-or-Miss Monte Carlo Quase-Aleatório',
    xaxis=dict(title='Valores Estimados'),
    yaxis=dict(title='Probabilidade'),
    bargap=0.1
)

# Adicionando uma linha para a média
linha_media = go.Scatter(
    x=[media, media],
    y=[0, 0.25],  # Ajuste conforme necessário
    mode='lines',
    line=dict(color='black', width=2, dash='dash'),
    name=f'Média: {media:.6f}'
)

# Adicionando linhas para o desvio padrão acima e abaixo da média
linha_desvio_superior = go.Scatter(
    x=[media + desvio_padrao, media + desvio_padrao],
    y=[0, 0.25],  # Ajuste conforme necessário
    mode='lines',
    line=dict(color='red', width=2, dash='dash'),  # Configuração da linha pontilhada
    name=f'Desvio Padrão: {desvio_padrao:.6f}'
)

linha_desvio_inferior = go.Scatter(
    x=[media - desvio_padrao, media - desvio_padrao],
    y=[0, 0.25],  # Ajuste conforme necessário
    mode='lines',
    line=dict(color='red', width=2, dash='dash'),  # Configuração da linha pontilhada
    showlegend=False
)

# Criando a figura
fig = go.Figure(data=[histograma, linha_media, linha_desvio_inferior, linha_desvio_superior], layout=layout)

# Mostrando o gráfico
fig.show()

In [145]:
lista = []
testes = 10**4
for m in range(testes):
    seed = int(time.time()) + m
    lista.append(hit_or_miss(f, a, b, 1000, 'pseudo', seed))

media = np.mean(lista)
desvio_padrao = np.std(lista)

# Criando o histograma com Plotly
histograma = go.Histogram(
    x=lista,
    histnorm='probability',
    marker_color='darkblue',
    opacity=0.75,
    showlegend=False
)

layout = go.Layout(
    title='Distribuição das Estimativas da Integral por Hit-or-Miss Monte Carlo Pseudo-Aleatório',
    xaxis=dict(title='Valores Estimados'),
    yaxis=dict(title='Probabilidade'),
    bargap=0.1
)

# Adicionando uma linha para a média
linha_media = go.Scatter(
    x=[media, media],
    y=[0, 0.06],  # Ajuste conforme necessário
    mode='lines',
    line=dict(color='black', width=2, dash='dash'),
    name=f'Média: {media:.6f}'
)

# Adicionando linhas para o desvio padrão acima e abaixo da média
linha_desvio_superior = go.Scatter(
    x=[media + desvio_padrao, media + desvio_padrao],
    y=[0, 0.06],  # Ajuste conforme necessário
    mode='lines',
    line=dict(color='red', width=2, dash='dash'),  # Configuração da linha pontilhada
    name=f'Desvio Padrão: {desvio_padrao:.6f}'
)

linha_desvio_inferior = go.Scatter(
    x=[media - desvio_padrao, media - desvio_padrao],
    y=[0, 0.06],  # Ajuste conforme necessário
    mode='lines',
    line=dict(color='red', width=2, dash='dash'),  # Configuração da linha pontilhada
    showlegend=False
)

# Criando a figura
fig = go.Figure(data=[histograma, linha_media, linha_desvio_inferior, linha_desvio_superior], layout=layout)

# Mostrando o gráfico
fig.show()

In [146]:
lista = []
testes = 10**4
for m in range(testes):
    seed = int(time.time()) + m
    lista.append(importance_sample_simplificado(f, a, b, 'gamma', 1000, 'quase', seed))

media = np.mean(lista)
desvio_padrao = np.std(lista)

# Criando o histograma com Plotly
histograma = go.Histogram(
    x=lista,
    histnorm='probability',
    marker_color='darkblue',
    opacity=0.75,
    showlegend=False
)

layout = go.Layout(
    title='Distribuição das Estimativas da Integral por Importance Sampling (Gamma) Monte Carlo Quase-Aleatório',
    xaxis=dict(title='Valores Estimados'),
    yaxis=dict(title='Probabilidade'),
    bargap=0.1
)

# Adicionando uma linha para a média
linha_media = go.Scatter(
    x=[media, media],
    y=[0, 0.05],  # Ajuste conforme necessário
    mode='lines',
    line=dict(color='black', width=2, dash='dash'),
    name=f'Média: {media:.6f}'
)

# Adicionando linhas para o desvio padrão acima e abaixo da média
linha_desvio_superior = go.Scatter(
    x=[media + desvio_padrao, media + desvio_padrao],
    y=[0, 0.05],  # Ajuste conforme necessário
    mode='lines',
    line=dict(color='red', width=2, dash='dash'),  # Configuração da linha pontilhada
    name=f'Desvio Padrão: {desvio_padrao:.6f}'
)

linha_desvio_inferior = go.Scatter(
    x=[media - desvio_padrao, media - desvio_padrao],
    y=[0, 0.05],  # Ajuste conforme necessário
    mode='lines',
    line=dict(color='red', width=2, dash='dash'),  # Configuração da linha pontilhada
    showlegend=False
)

# Criando a figura
fig = go.Figure(data=[histograma, linha_media, linha_desvio_inferior, linha_desvio_superior], layout=layout)

# Mostrando o gráfico
fig.show()

In [147]:
lista = []
testes = 10**4
for m in range(testes):
    seed = int(time.time()) + m
    lista.append(importance_sample_simplificado(f, a, b, 'gamma', 1000, 'pseudo', seed))

media = np.mean(lista)
desvio_padrao = np.std(lista)

# Criando o histograma com Plotly
histograma = go.Histogram(
    x=lista,
    histnorm='probability',
    marker_color='darkblue',
    opacity=0.75,
    showlegend=False
)

layout = go.Layout(
    title='Distribuição das Estimativas da Integral por Importance Sampling (Gamma) Monte Carlo Pseudo-Aleatório',
    xaxis=dict(title='Valores Estimados'),
    yaxis=dict(title='Probabilidade'),
    bargap=0.1
)

# Adicionando uma linha para a média
linha_media = go.Scatter(
    x=[media, media],
    y=[0, 0.05],  # Ajuste conforme necessário
    mode='lines',
    line=dict(color='black', width=2, dash='dash'),
    name=f'Média: {media:.6f}'
)

# Adicionando linhas para o desvio padrão acima e abaixo da média
linha_desvio_superior = go.Scatter(
    x=[media + desvio_padrao, media + desvio_padrao],
    y=[0, 0.05],  # Ajuste conforme necessário
    mode='lines',
    line=dict(color='red', width=2, dash='dash'),  # Configuração da linha pontilhada
    name=f'Desvio Padrão: {desvio_padrao:.6f}'
)

linha_desvio_inferior = go.Scatter(
    x=[media - desvio_padrao, media - desvio_padrao],
    y=[0, 0.05],  # Ajuste conforme necessário
    mode='lines',
    line=dict(color='red', width=2, dash='dash'),  # Configuração da linha pontilhada
    showlegend=False
)

# Criando a figura
fig = go.Figure(data=[histograma, linha_media, linha_desvio_inferior, linha_desvio_superior], layout=layout)

# Mostrando o gráfico
fig.show()

In [148]:
lista = []
testes = 10**5
for m in range(testes):
    seed = int(time.time()) + m
    lista.append(control_variate(f, a, b, p, x_0, 1000, 'quase', seed))

media = np.mean(lista)
desvio_padrao = np.std(lista)

# Criando o histograma com Plotly
histograma = go.Histogram(
    x=lista,
    histnorm='probability',
    marker_color='darkblue',
    opacity=0.75,
    showlegend=False
)

layout = go.Layout(
    title='Distribuição das Estimativas da Integral por Control Variate Monte Carlo Quase-Aleatório',
    xaxis=dict(title='Valores Estimados'),
    yaxis=dict(title='Probabilidade'),
    bargap=0.1
)

# Adicionando uma linha para a média
linha_media = go.Scatter(
    x=[media, media],
    y=[0, 0.05],  # Ajuste conforme necessário
    mode='lines',
    line=dict(color='black', width=2, dash='dash'),
    name=f'Média: {media:.6f}'
)

# Adicionando linhas para o desvio padrão acima e abaixo da média
linha_desvio_superior = go.Scatter(
    x=[media + desvio_padrao, media + desvio_padrao],
    y=[0, 0.05],  # Ajuste conforme necessário
    mode='lines',
    line=dict(color='red', width=2, dash='dash'),  # Configuração da linha pontilhada
    name=f'Desvio Padrão: {desvio_padrao:.6f}'
)

linha_desvio_inferior = go.Scatter(
    x=[media - desvio_padrao, media - desvio_padrao],
    y=[0, 0.05],  # Ajuste conforme necessário
    mode='lines',
    line=dict(color='red', width=2, dash='dash'),  # Configuração da linha pontilhada
    showlegend=False
)

# Criando a figura
fig = go.Figure(data=[histograma, linha_media, linha_desvio_inferior, linha_desvio_superior], layout=layout)

# Mostrando o gráfico
fig.show()

### **Análise de Variância por Método**

In [9]:
# Crude Monte Carlo
valor_real = 0.9217620390808
seed = int(time.time())
sampler = qmc.Halton(d=1, scramble=True, seed=seed)
lista_x = sampler.random(n)
soma = 0

variância = np.mean((f(lista_x, a, b) - valor_real)**2)/n
variância

1.96669122797924e-08

In [150]:
# Hit-or-Miss
variância = valor_real*(1 - valor_real)/n
variância

7.211678239040573e-07

In [151]:
# Importance Sampling (Gamma)
valor_real = 0.9217620390808
seed = int(time.time())
sampler = qmc.Halton(d=1, scramble=True, seed=seed)
lista_x = sampler.random(n)
soma = 0

variância = np.mean(((f(lista_x, a, b)/gamma(lista_x, 1.000, 6.475)) - valor_real)**2 * gamma(lista_x, 1.000, 6.475))/n
variância

1.0762153319437556e-10

In [152]:
# Importance Sampling (Beta)
valor_real = 0.9217620390808
seed = int(time.time())
sampler = qmc.Halton(d=1, scramble=True, seed=seed)
lista_x = sampler.random(n)
soma = 0

variância = np.mean(((f(lista_x, a, b)/beta(lista_x, 0.972, 1.016)) - valor_real)**2 * gamma(lista_x, 1.000, 6.475))/n
variância

2.2833608952027984e-09

In [153]:
# Importance Sampling (Weibull)
valor_real = 0.9217620390808
seed = int(time.time())
sampler = qmc.Halton(d=1, scramble=True, seed=seed)
lista_x = sampler.random(n)
soma = 0

variância = np.mean(((f(lista_x, a, b)/weibull(lista_x, 1.000, 6.488)) - valor_real)**2 * gamma(lista_x, 1.000, 6.475))/n
variância

1.1306047750904491e-10

In [154]:
# Control Variate
valor_real = 0.9217620390808
seed = int(time.time())
sampler = qmc.Halton(d=1, scramble=True, seed=seed)
lista_x = sampler.random(n)
lista_y_f = f(lista_x, a, b)
lista_y_p = p(lista_x, x_0, f, a, b)
correlacao = 0.9998952458

variância_f = np.std(lista_y_f)**2
variância_p = np.std(lista_y_p)**2
variância = (1/n)*(variância_f + variância_p - 2*correlacao*(variância_f*variância_p)**(1/2))
variância

4.1201739720778816e-12